# Scraping Yahoo Finance for Price Data
This notebook is the cleaned version that will take the large insider_trading.csv file and uses it to query the yahoo finance API to pull out price data. The goal is to obtain all historical price data for each unique symbol, calculate a 21 day moving average of close prices to see a smoothed trend of price data. We will then look at the price a month prior to the insider transaction, and every month after for six months. Along with the price data, we will calculate an average rate of change for the moving average over that monthly period. (i.e. the stock price has increased 0.5% per day for the month between transction and the close price one month later). It will add all of this data dynmically to the initial dataset and then save an intermediate .csv file that can be used for replication and reproducibility.

# Section 1: Connecting To Goolge Colab and Google Drive
All of our data is being kept on a shared google drive and we are using google colab for our data collection and analysis. This section will briefly go over connecting to the drive and accessing the proper directory.

In [ ]:
#Start by importing drive from google.colab
from google.colab import drive
import os

#Mount the drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
#Students Google Drive Path
toms_path = '/content/drive/MyDrive/Colab Notebooks/593 - Milestone I/593 - Insider Trading Milestone I Project'
kirts_path = None
ramis_path = None

#Navigate to the right working directory and confirm our current working drive
os.chdir(toms_path)
#os.chdir(kirts_path)
#os.chdir(ramis_path)
print(os.getcwd())

/content/drive/MyDrive/Colab Notebooks/593 - Milestone I/593 - Insider Trading Milestone I Project


# Section 2: Importing Libraries and Capturing Dependencies
This section will hold all of the libraries that we will be using for data import, manipulation, and analysis. We will then capture the versions of all libriaries for reproducibility with our code. Unforutnately, google colab uses an outdated yfinance, so let's explicity install the upgraded library first and restart the kernel.

In [ ]:
#Let's explicity update yfiance just incase
!pip install yfinance --upgrade --no-cache-dir

In [ ]:
#Data import
import numpy as np
import pandas as pd
import time
from datetime import timedelta, date, datetime
import yfinance as yf

Let's print out the versions that we are using (or save a file).

In [ ]:
#print the dependencies in the notebook
!pip freeze

#create a .txt file that contains all versions
#!pip freeze > colab_requirements.txt

absl-py==1.4.0
accelerate==1.6.0
aiohappyeyeballs==2.6.1
aiohttp==3.11.15
aiosignal==1.3.2
alabaster==1.0.0
albucore==0.0.24
albumentations==2.0.6
ale-py==0.11.0
altair==5.5.0
annotated-types==0.7.0
antlr4-python3-runtime==4.9.3
anyio==4.9.0
argon2-cffi==23.1.0
argon2-cffi-bindings==21.2.0
array_record==0.7.2
arviz==0.21.0
astropy==7.0.2
astropy-iers-data==0.2025.5.12.0.38.29
astunparse==1.6.3
atpublic==5.1
attrs==25.3.0
audioread==3.0.1
autograd==1.8.0
babel==2.17.0
backcall==0.2.0
backports.tarfile==1.2.0
beautifulsoup4==4.13.4
betterproto==2.0.0b6
bigframes==2.4.0
bigquery-magics==0.9.0
bleach==6.2.0
blinker==1.9.0
blis==1.3.0
blobfile==3.0.0
blosc2==3.3.2
bokeh==3.7.3
Bottleneck==1.4.2
bqplot==0.12.44
branca==0.8.1
build==1.2.2.post1
CacheControl==0.14.3
cachetools==5.5.2
catalogue==2.0.10
certifi==2025.4.26
cffi==1.17.1
chardet==5.2.0
charset-normalizer==3.4.2
chex==0.1.89
clarabel==0.10.0
click==8.2.0
cloudpathlib==0.21.0
cloudpickle==3.1.1
cmake==3.31.6
cmdstanpy==1.2.5
colorcet

# Section 3: Importing Insider Transaction Data and Cleaning
In this section we will import the large .CSV file that combines all insider transactions from Q1 2006 to Q4 2024. We will be using this file to pull as much price data from yfinance as we can and will be the basis of our combined datasets.

In [ ]:
#Start by taking a quick look at the files in our directory so we can pull the right one
print(os.listdir())

['insider_transactions_readme[1].pdf', 'parse_form4.py', 'colab_requirements.txt', 'all_common_stock_purchases (6).csv', 'all_common_stock_purchases (6).gsheet', 'Mounting_Notebook_Importing_Form4.ipynb', 'Insider transaction data sets', 'Meeting Summaries', 'Insiders_multi_zip.ipynb', "Insider Trading: Do Corporate Insiders Know Something We Don't?.docx", 'Insider Trading Proposal.docx', 'all_common_stock_purchases 2006 to 4Q24.csv', 'sec_insider_zips', 'Insiders_zip_data_processing.ipynb', 'stock_purchases_by_insider.csv', 'Market_Cap_Sector_Industry_Classification.ipynb', 'download_sec_zips.ipynb', 'common_stock_purchases_with_price_data.csv', 'yahoo_finance_price_data.ipynb']


In [ ]:
#Read in the .csv file
cs_df = pd.read_csv('all_common_stock_purchases 2006 to 4Q24.csv')
print(f"Let's take a look at the size of our dataframe: {cs_df.shape}\n")
#print(cs_df.head())

#Let's start by removing any data where tickers == None
cs_df = cs_df[cs_df['Ticker'] != 'NONE']
cs_df = cs_df[cs_df['Ticker'] != 'None']

#Let's also drop any column that is missing the ticker or the price per share or any shares purchased
cs_df = cs_df[~cs_df['Ticker'].isna()].copy()
cs_df = cs_df[~cs_df['Price per Share'].isna()].copy()
cs_df = cs_df[cs_df['Shares'] > 0.0]

#Let's fill missing insider titles, names and issuers with a string for the group by statement
cs_df[['Insider Title','Insider Name','Issuer']] = cs_df[['Insider Title','Insider Name','Issuer']].fillna('Missing')
print(f"After removing transction with no tickers we have {cs_df.shape}\n")

#Let's take a look at the number of unique tickers in this file
tickers = list(cs_df['Ticker'].unique())
print(f"We have {len(tickers)} unique tickers\n")

#Let's take a look at the number of missing values in the file
missing_counts = cs_df.isna().sum()
print(missing_counts)

Let's take a look at the size of our dataframe: (463300, 15)

After removing transction with no tickers we have (455688, 15)

We have 11068 unique tickers

Insider Name          0
Insider Title         0
Insider Role          0
Issuer                0
Ticker                0
CIK Code              0
Period of Report      0
Transaction Date      0
Security              0
Transaction Code      0
Shares                0
Price per Share       0
Shares After        174
Ownership Type        0
ACCESSION_NUMBER      0
dtype: int64


There are multiple transactions that occur by the same insider on the same day. This is to account for shares purchased at different prices. We can combine these together using groupby in order to reduce the size of the dataframe and our compute. First, we need to calculate the average price per share. We will do this by multiply the 'Shares' column by the 'Price per Share' column to see the total capital invested for the day. We will then divide that by the total capital to get 'average price per share' after our grouping. We will group by the categorical columns, the numerical columns will have different aggregation functions based on what they represent. Shares will be summed for the day, We will take the average price per share (but likely wont use this as it wont be accurate), we will take the max of shares after to see the highest amount of shares they had at the end of the transactions period and we will sum the total capital invested to find the true average cost per share.

In [ ]:
#Let's calcualte the capital invested for each individual transaction
cs_df['total_capital'] = cs_df['Shares'] * cs_df['Price per Share']

#Let's group the dataframe so that we get all transactions on the same day by the same insider as a single transaction
grouped_df = cs_df.groupby(['Insider Name',
                            'Insider Title',
                            'Insider Role',
                            'Issuer',
                            'Ticker',
                            'CIK Code',
                            'Period of Report',
                            'Transaction Date',
                            'Security',
                            'Transaction Code',
                            'Ownership Type',
                            'ACCESSION_NUMBER'],
                           as_index=False).agg(shares = ('Shares','sum'),
                                               price_per_share = ('Price per Share','mean'),
                                               shares_after = ('Shares After','max'),
                                               total_capital = ('total_capital','sum'))
#Now, we can find the average price per share
grouped_df['average_price_per_share'] = grouped_df['total_capital'] / grouped_df['shares']
print(grouped_df.shape)
grouped_df.head()

(288615, 17)


Insider Name Insider Title  \
0                       2180 ASSOCIATES FUND VII L P       Missing   
1                                              3M CO       Missing   
2                      4D GLOBAL ENERGY ADVISORS SAS       Missing   
3                   4D GLOBAL ENERGY INVESTMENTS PLC       Missing   
4  7-2010 GRAT 6 UNDER KENT C MCCARTHY GRAT TR DT...       Missing   

           Insider Role                                Issuer    Ticker  \
0       Tenpercentowner                             ON24 INC.      ONTF   
1       Tenpercentowner                   ARTIFICIAL LIFE INC   ALIF.OB   
2       Tenpercentowner  Independence Contract Drilling, Inc.       ICD   
3       Tenpercentowner  Independence Contract Drilling, Inc.       ICD   
4  Tenpercentownerother                 China Cord Blood Corp  NYSE: CO   

   CIK Code Period of Report Transaction Date      Security Transaction Code  \
0   1110611         5-Feb-21         5-Feb-21  Common Stock                P   
1   1070361        23-Oct-09        23-Oct-09  Common Stock                P   
2   1537028        13-Aug-14        13-Aug-14  Common Stock                P   
3   1537028        13-Aug-14        13-Aug-14  Common Stock                P   
4   1467808        19-Nov-14        19-Nov-14  Common Stock                P   

  Ownership Type      ACCESSION_NUMBER     shares  price_per_share  \
0              I  0001527715-21-000003     5000.0             50.0   
1              D  0001104659-09-060540  6447491.0              1.0   
2              I  0001209191-14-052787   600000.0             11.0   
3              I  0001209191-14-052787   600000.0             11.0   
4              I  0001140361-14-043121     4617.0              4.8   

   shares_after  total_capital  average_price_per_share  
0        5000.0       250000.0                     50.0  
1     6447491.0      6447491.0                      1.0  
2     2562500.0      6600000.0                     11.0  
3     2562500.0      6600000.0                     11.0  
4    10018563.0        22161.6                      4.8

Finally, we need to prepare this dataframe for our new data columns that we will be adding. It will be easier to create them now and fill them in as we iterate through the symbols to avoid throwing errors. So we will do that now.

In [ ]:
new_columns = ['price_-1month','trend_-1month','transactiondate_high','transactiondate_low','trend_transactiondate','price_1month','trend_1month','price_2month','trend_2month','price_3month','trend_3month','price_4month','trend_4month','price_5month','trend_5month','price_6month','trend_6month']
for col in new_columns:
    grouped_df[col] = pd.NA
print(grouped_df.shape)
grouped_df.head()

(288615, 32)


Insider Name Insider Title  \
0                       2180 ASSOCIATES FUND VII L P       Missing   
1                                              3M CO       Missing   
2                      4D GLOBAL ENERGY ADVISORS SAS       Missing   
3                   4D GLOBAL ENERGY INVESTMENTS PLC       Missing   
4  7-2010 GRAT 6 UNDER KENT C MCCARTHY GRAT TR DT...       Missing   

           Insider Role                                Issuer    Ticker  \
0       Tenpercentowner                             ON24 INC.      ONTF   
1       Tenpercentowner                   ARTIFICIAL LIFE INC   ALIF.OB   
2       Tenpercentowner  Independence Contract Drilling, Inc.       ICD   
3       Tenpercentowner  Independence Contract Drilling, Inc.       ICD   
4  Tenpercentownerother                 China Cord Blood Corp  NYSE: CO   

   CIK Code Period of Report Transaction Date      Security Transaction Code  \
0   1110611         5-Feb-21         5-Feb-21  Common Stock                P   
1   1070361        23-Oct-09        23-Oct-09  Common Stock                P   
2   1537028        13-Aug-14        13-Aug-14  Common Stock                P   
3   1537028        13-Aug-14        13-Aug-14  Common Stock                P   
4   1467808        19-Nov-14        19-Nov-14  Common Stock                P   

   ... price_2month trend_2month  price_3month  trend_3month  price_4month  \
0  ...         <NA>         <NA>          <NA>          <NA>          <NA>   
1  ...         <NA>         <NA>          <NA>          <NA>          <NA>   
2  ...         <NA>         <NA>          <NA>          <NA>          <NA>   
3  ...         <NA>         <NA>          <NA>          <NA>          <NA>   
4  ...         <NA>         <NA>          <NA>          <NA>          <NA>   

   trend_4month  price_5month trend_5month price_6month trend_6month  
0          <NA>          <NA>         <NA>         <NA>         <NA>  
1          <NA>          <NA>         <NA>         <NA>         <NA>  
2          <NA>          <NA>         <NA>         <NA>         <NA>  
3          <NA>          <NA>         <NA>         <NA>         <NA>  
4          <NA>          <NA>         <NA>         <NA>         <NA>  

[5 rows x 32 columns]

# Section 4: Yahoo Finance API and Data Aggregation
The data frame is ready for us to query the yfinance API to start pulling in data. This will likely take a significant period of time due to how much data we are trying to pull, I am going to use a magic command to time how long this truly takes.

In [ ]:
%%time

#let's bring in the yahoo finance API and datetime
import yfinance as yf
import time
from datetime import timedelta, date, datetime

#Now we can use the ticker to request that complete historical data for this ticker
for ticker in tickers:
    try:
        #The first the we need to do is find all of the transactions with this ticker
        print(f"\nProcsessing ticker {ticker}...")
        temp_df = grouped_df.loc[grouped_df['Ticker'] == ticker].copy()
        #Now that we have a temporary dataframe, we can pull the price data
        ticker_data = yf.download(tickers = ticker, period = 'max',interval = '1d',auto_adjust=True, actions=False, threads = False)
        #Let's calculate the moving avearge
        ticker_data['28MA'] = ticker_data['Close'].rolling(window=28).mean()
        #Let's normalize it based on the previous value of the MA
        ticker_data['MA_diff'] = ticker_data['28MA'].pct_change() * 100
        ticker_data = ticker_data.dropna().copy()
        #Finally, I want to take the rolling average of that MA_diff (momentum of momentum change) over the last 28 days so we get the monthly trend
        ticker_data['MA_trend'] = ticker_data['MA_diff'].rolling(window=28).mean()
        ticker_data = ticker_data.dropna().copy()
        ticker_data.index = pd.to_datetime(ticker_data.index)
        #Now, we will have to iterate through the rows to fill them out individually
        for index, row in temp_df.iterrows():
            #This is where we will need to grab the values and the index and populate the orginal dataframe (grouped_df)
            #Find out the date of the transaction (specify the format explicitly)
            trans_date = pd.to_datetime(row['Transaction Date'], format = "%d-%b-%y")

            #Let's start by defining all of our dates
            date_premonth = (trans_date - pd.DateOffset(months=1))
            date_onemonth = (trans_date + pd.DateOffset(months=1))
            date_twomonth = (trans_date + pd.DateOffset(months=2))
            date_threemonth = (trans_date + pd.DateOffset(months=3))
            date_fourmonth = (trans_date + pd.DateOffset(months=4))
            date_fivemonth = (trans_date + pd.DateOffset(months=5))
            date_sixmonth = (trans_date + pd.DateOffset(months=6))

            #Let's Get all of the prices at the right timepoints we will use .asof because we likely only have trading days
            price_premonth = np.round(ticker_data['Close'][ticker].asof(date_premonth),2)
            price_onemonth = np.round(ticker_data['Close'][ticker].asof(date_onemonth),2)
            price_twomonth = np.round(ticker_data['Close'][ticker].asof(date_twomonth),2)
            price_threemonth = np.round(ticker_data['Close'][ticker].asof(date_threemonth),2)
            price_fourmonth = np.round(ticker_data['Close'][ticker].asof(date_fourmonth),2)
            price_fivemonth = np.round(ticker_data['Close'][ticker].asof(date_fivemonth),2)
            price_sixmonth = np.round(ticker_data['Close'][ticker].asof(date_sixmonth),2)

            #Let's bring in the high and low of the transaction date so we can verify the buy price was on that day
            high_transactiondate = np.round(ticker_data['High'][ticker].asof(trans_date),2)
            low_transactiondate = np.round(ticker_data['Low'][ticker].asof(trans_date),2)

            #Let's get the momentum of all the trends
            trend_premonth = np.round(ticker_data['MA_trend'].asof(date_premonth),4)
            trend_transactiondate = np.round(ticker_data['MA_trend'].asof(trans_date),4)
            trend_onemonth = np.round(ticker_data['MA_trend'].asof(date_onemonth),4)
            trend_twomonth = np.round(ticker_data['MA_trend'].asof(date_twomonth),4)
            trend_threemonth = np.round(ticker_data['MA_trend'].asof(date_threemonth),4)
            trend_fourmonth = np.round(ticker_data['MA_trend'].asof(date_fourmonth),4)
            trend_fivemonth = np.round(ticker_data['MA_trend'].asof(date_fivemonth),4)
            trend_sixmonth = np.round(ticker_data['MA_trend'].asof(date_sixmonth),4)

            #Grab todays date
            today = pd.to_datetime(date.today())

            #Let's see if we can change the original dataframe with these new values (we will use .at because its faster and replaces copies)

            grouped_df.at[index,'price_-1month'] = price_premonth
            grouped_df.at[index,'transactiondate_high'] = high_transactiondate
            grouped_df.at[index,'transactiondate_low'] = low_transactiondate

            if date_onemonth < today:
                grouped_df.at[index,'price_1month'] = price_onemonth
            if date_twomonth < today:
                grouped_df.at[index,'price_2month'] = price_twomonth
            if date_threemonth < today:
                grouped_df.at[index,'price_3month'] = price_threemonth
            if date_fourmonth < today:
                grouped_df.at[index,'price_4month'] = price_fourmonth
            if date_fivemonth < today:
                grouped_df.at[index,'price_5month'] = price_fivemonth
            if date_sixmonth < today:
                grouped_df.at[index,'price_6month'] = price_sixmonth

            #Let's add the price trend data as well
            grouped_df.at[index,'trend_-1month'] = trend_premonth
            grouped_df.at[index,'trend_transactiondate'] = trend_transactiondate
            if date_onemonth < today:
                grouped_df.at[index,'trend_1month'] = trend_onemonth
            if date_twomonth < today:
                grouped_df.at[index,'trend_2month'] = trend_twomonth
            if date_threemonth < today:
                grouped_df.at[index,'trend_3month'] = trend_threemonth
            if date_fourmonth < today:
                grouped_df.at[index,'trend_4month'] = trend_fourmonth
            if date_fivemonth < today:
                grouped_df.at[index,'trend_5month'] = trend_fivemonth
            if date_sixmonth < today:
                grouped_df.at[index,'trend_6month'] = trend_sixmonth

        time.sleep(0.5)
    except:
        print(f"Failed to extract data for {ticker} from Yahoo Finance")


Procsessing ticker ADBE...


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['CVBT']: YFPricesMissingError('possibly delisted; no price data found  (1d 1926-06-11 -> 2025-05-17)')



Procsessing ticker CVBT...
Failed to extract data for CVBT from Yahoo Finance

Procsessing ticker EUBK...


[*********************100%***********************]  1 of 1 completed
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['EUBK']: YFPricesMissingError('possibly delisted; no price data found  (1d 1926-06-11 -> 2025-05-17)')
[*********************100%***********************]  1 of 1 completed


Failed to extract data for EUBK from Yahoo Finance

Procsessing ticker ENPT...
Failed to extract data for ENPT from Yahoo Finance

Procsessing ticker SPCBF...


...

Failed to extract data for BPSK from Yahoo Finance

Procsessing ticker IMNN...


[*********************100%***********************]  1 of 1 completed



Procsessing ticker FXBY...


[*********************100%***********************]  1 of 1 completed


CPU times: user 54min 32s, sys: 1min 6s, total: 55min 39s
Wall time: 1h 57min 37s


On our first run, it is likely that we will find a significant number of errors due to tickers being delisted, etc through the financial crisis and other times of significant market constriction. We will do a rough calculation on the number of valid tickers we were able to obtain to make sure we don't have too much of a bias. Here is a list of common Errors we encountered:

Errors:
- Unidentified characters in 'NYSE/TRN' (may need to split)
- possibly delisted (Can't do anything about that)
- Failed to download ticker 'N O G' (potentially due to spaces)
- Failed to download HEI.A (possibly delisted)
- Failed to extract data... (may re-try?)

We started with 11068 unique tickers stored in the variable 'tickers'. Let's see the size of our dataframe and how many tickers we were able to keep after removing data that we were unable to pull. We are determining tickers that we were unable to pull by looking for NA values in the 'price--1month' column as that is the first datapoint to be filled.

In [ ]:
print(grouped_df.shape)
filtered_df = grouped_df[~grouped_df['price_-1month'].isna()]
print(filtered_df.shape)
uni_tick = filtered_df['Ticker'].unique()
print(len(uni_tick))
print(f'We kept {np.round(len(uni_tick)/len(tickers)*100,1)}% of the tickers for this quarter')

(288615, 32)
(122067, 32)
3595
We kept 32.5% of the tickers for this quarter


In [ ]:
#Let's take a look at the number of missing values in the file
missing_counts = filtered_df.isna().sum()
print(missing_counts)

#Let's look at a random sample of 15 of these entries
filtered_df.sample(15)

Insider Name                  0
Insider Title                 0
Insider Role                  0
Issuer                        0
Ticker                        0
CIK Code                      0
Period of Report              0
Transaction Date              0
Security                      0
Transaction Code              0
Ownership Type                0
ACCESSION_NUMBER              0
shares                        0
price_per_share               0
shares_after                 44
total_capital                 0
average_price_per_share     539
price_-1month                 0
trend_-1month                 0
trend_transactiondate         0
price_1month                  4
trend_1month                  4
price_2month                185
trend_2month                185
price_3month                828
trend_3month                828
price_4month               1126
trend_4month               1126
price_5month               1454
trend_5month               1454
price_6month               2172
trend_6m

Insider Name                  Insider Title      Insider Role  \
214283          RIBEIRO CARL                        Missing          Director   
185039      MURPHY MICHAEL R                        Missing   Tenpercentowner   
92004      GIBSON JAMES W JR                        Missing          Director   
16897             BARR DAVID                        Missing          Director   
62359       DOERFERT KIRSTEN            Sr VP and Gen'l Mgr           Officer   
185527       MUSHAKOV ANDREY  EVP - Intl Nuclear Operations           Officer   
277431      WHITE RAYMOND T.                        Missing   Tenpercentowner   
245764       SORENSEN VAGN O                        Missing          Director   
23552        BEST LAWRENCE C                        Missing          Director   
130584  KAMPIZIONES ANDREW G                        Missing          Director   
39283           BURNETT VERA                    Interim CFO           Officer   
14632        BALAOURAS PARIS      Chief Cultivation Officer  Director,Officer   
91145          GHAURI NAJEEB                            CEO  Director,Officer   
55426        DANTONI DAVID J                        Missing          Director   
150157  LECHLEITER RICHARD A                        Missing          Director   

                                    Issuer Ticker  CIK Code Period of Report  \
214283               INDEPENDENT BANK CORP   INDB    776901        25-Jan-11   
185039                      AtriCure, Inc.   ATRC   1323885         3-Jan-11   
92004            COMMUNITY BANK SYSTEM INC    CBU    723188         9-Aug-11   
16897           Builders FirstSource, Inc.   BLDR   1316835        16-May-12   
62359                         UROLOGIX INC   ULGX    882873        30-Oct-07   
185527                    LIGHTBRIDGE Corp   LTBR   1084554        25-Nov-16   
277431                       FOSTER L B CO   FSTR    352825        25-Apr-18   
245764         ROYAL CARIBBEAN CRUISES LTD    RCL    884887         1-Aug-11   
23552                     HAEMONETICS CORP    HAE    313143        22-Aug-03   
130584       FIRST RELIANCE BANCSHARES INC   FSRL   1172102        31-Dec-08   
39283                          ENNIS, INC.    EBF     33002        13-May-21   
14632                    MJ Holdings, Inc.   MJNE   1456857        27-Jul-22   
91145              NETSOL TECHNOLOGIES INC   NTWK   1039280        17-May-21   
55426   COMPASS MINERALS INTERNATIONAL INC    CMP   1227654         3-May-07   
150157                     S Y BANCORP INC   SYBT    835324         1-Oct-10   

       Transaction Date      Security Transaction Code  ... price_2month  \
214283        25-Jan-11  Common Stock                P  ...        17.79   
185039         4-Jan-11  Common Stock                P  ...        10.01   
92004          9-Aug-11  Common Stock                P  ...        15.01   
16897         18-May-12  Common Stock                P  ...         4.86   
62359         30-Oct-07  Common Stock                P  ...         1.14   
185527        25-Nov-16  Common Stock                P  ...        12.84   
277431        25-Apr-18  Common Stock                P  ...         24.1   
245764         1-Aug-11  Common Stock                P  ...        18.11   
23552         16-Jun-06  Common Stock                P  ...        23.69   
130584        24-Oct-08  Common Stock                P  ...         5.25   
39283         13-May-21  Common Stock                P  ...        15.07   
14632         27-Jul-22  Common Stock                P  ...         0.23   
91145         17-May-21  Common Stock                P  ...         4.16   
55426          3-May-07  Common Stock                P  ...        20.76   
150157         1-Oct-10  Common Stock                P  ...        10.88   

       trend_2month  price_3month  trend_3month  price_4month  trend_4month  \
214283      -0.1493         19.07         0.009         19.83        0.3035   
185039       0.1005         11.61       -0.2008         12.36  

# Section 5: Save an Intermediate .CSV file
Let's save another intermediate .CSV file that we can use for reproducibility in our study.


In [ ]:
filtered_df.to_csv('common_stock_purchases_with_price_data.csv',index=False)